In [1]:
import requests
import xml.etree.ElementTree as ET

In [2]:
import pandas as pd
import numpy as np

import requests

from lxml import html
from bs4 import BeautifulSoup

import re

import finance.helpers as hlp
# from finance import yahoo

In [7]:
engine = hlp.load_db('yahoo')
scn = pd.read_sql('SELECT * FROM screener;', con=engine, index_col='Symbol')

https://github.com/areed1192/sigma_coding_youtube/blob/master/python/python-finance/sec-web-scraping/Web%20Scraping%20SEC%20-%20Parsing%20SEC%20Documents%20-%20New%20Filings.ipynb

In [226]:
class Edgar:

    _request_headers = {
        'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/93.0.4577.82 Safari/537.36'
        }
    def __init__(self,
                 ticker,
                 filings=['10-K', '10-Q'],
                 date_beg=None #'20000101'
                ):
        '''
        Object for SEC Edgar data
        '''
        
        # make sure filings is not string
        if type(filings) == str:
            filings = [filings]
            
        # information about company
        self.ticker = ticker
        self.filings = filings
        
        # to be filled in when gathering documents
        self.company_name = ''
        self.cik = ''
        
        # edgar urls
        self._base = 'https://sec.gov'
        self._search_urls = []

        
        # gather documents
        docs = []
        for filing in filings:
            
            # search string
            search_url = f'{self._base}/cgi-bin/browse-edgar?action=getcompany&CIK={self.ticker}&type={filing}'

            # add beginning date
            if date_beg:
                search_url += f'&dateb={date_beg}'
            
            # save search url
            self._search_urls.append(search_url)

            # query request
            resp = requests.get(search_url, headers=self._request_headers)
            query_doc = html.fromstring(resp.content)
            
            # get queried documents
            docs.append(self._get_documents(query_doc))

            # get company name and CIK
            company_el = query_doc.xpath('//span[@class="companyName"]')

            if company_el:
                self.company_name = company_el[0].text.strip()
                self.cik = company_el[0].xpath('./a')[0].text.split()[0]

        # documents
        self.documents = pd.concat(docs).sort_index(ascending=False)
        
        # property
        self._data_files = None
        
    def __repr__(self):
        
        return f"<SEC Edgar {self.cik} [{self.ticker}][{self.company_name}][{', '.join(self.filings)}]>"
    

    def _get_documents(self, query_doc):

        query_results = query_doc.xpath('//table[@summary="Results"]')

        # no results
        if not query_results:
            return []

        # table element
        table_el = query_results[0]

        # get table headers
        ths = [th.text for th in table_el.xpath('.//th')]

        # result dicts
        res = {th:[] for th in ths}
        res.update({'Url' : [], 'Interactive' : []}) # for url
        
        # iterate through rows
        for tr in table_el.xpath('.//tr'):

            # table data elements
            td_els = tr.xpath('.//td')

            # get data from 
            for el, th in zip(td_els, ths):
                td = el.text_content().strip()
                if td:
                    res[th].append(td.strip())
                else:
                    res[th].append(np.nan)

            # add url
            docs_els = tr.xpath('./td/a[contains(@id,"documents")]')
            if docs_els:
                res['Url'].append(self._base + docs_els[0].get('href'))

                # interactive data for excel
                intv_els = tr.xpath('./td/a[contains(@id,"interactive")]')
                if intv_els:
                    # add interactive data url
                    intv_url = self._base+intv_els[0].get('href')
                    res['Interactive'].append(intv_url)
                else:
                    res['Interactive'].append(np.nan)


        # pandas result
        df = pd.DataFrame(res)
        key = 'Filing Date'
        df[key] = pd.to_datetime(df[key])

        return df.set_index(key)
    
    @property
    def data_files(self):
        
        if self._data_files is None:
            self._data_files = self._get_data_files()
        
        return self._data_files
    
    def _get_data_files(self):

        print('Getting data files...')
        
        xml_docs = {}

        ndocs = len(self.documents)
        for i, url in enumerate(self.documents['Url']):

            resp = requests.get(url, headers=self._request_headers)
            filing_doc = html.fromstring(resp.content)

            data_files = filing_doc.xpath('.//table[@summary="Data Files"]')

            if data_files:
                table_el = data_files[0]

                # get table headers
                ths = [th.text for th in table_el.xpath('.//th')]

                # result dicts
                res = {th:[] for th in ths}
                res['Url'] = []

                # iterate through rows
                for tr in table_el.xpath('.//tr'):

                    # table data elements
                    td_els = tr.xpath('.//td')

                    # get data from 
                    for el, th in zip(td_els, ths):

                        td = el.text_content().strip()
                        if td:
                            res[th].append(td.strip())
                        else:
                            res[th].append(np.nan)

                    a = tr.xpath('./td/a')
                    if a:
                        res['Url'].append(self._base + a[0].get('href'))

            xml_docs[url] = {k : v for k, v in zip(res['Type'], res['Url'])}

        df = pd.DataFrame(xml_docs).T
        df['EX-101.INS'] = df[['EX-101.INS', 'XML']].bfill(axis=1).iloc[:, 0]
        df = df[[col for col in df.columns if 'EX' in col]]
        df.columns = [col.replace('EX-101.', '') for col in df.columns]

        return pd.merge(self.documents, df, left_on='Url', right_index=True)

In [227]:
self = Edgar('AAPL', filings=['10-K'])

In [228]:
self

<SEC Edgar 0000320193 [AAPL][Apple Inc.][10-K]>

In [229]:
self.documents

Filings                        Format  \
Filing Date                                          
2020-10-30      10-K  Documents   Interactive Data   
2019-10-31      10-K  Documents   Interactive Data   
2018-11-05      10-K  Documents   Interactive Data   
2017-11-03      10-K  Documents   Interactive Data   
2016-10-26      10-K  Documents   Interactive Data   
2015-10-28      10-K  Documents   Interactive Data   
2014-10-27      10-K  Documents   Interactive Data   
2013-10-30      10-K  Documents   Interactive Data   
2012-10-31      10-K  Documents   Interactive Data   
2011-10-26      10-K  Documents   Interactive Data   
2010-10-27      10-K  Documents   Interactive Data   
2010-01-25    10-K/A  Documents   Interactive Data   
2009-10-27      10-K  Documents   Interactive Data   
2008-11-05      10-K                     Documents   
2007-11-15      10-K                     Documents   
2006-12-29      10-K                     Documents   
2005-12-01      10-K                     Documents   
2004-12-03      10-K                     Documents   
2003-12-19      10-K                     Documents   
2002-12-19      10-K                     Documents   
2001-12-21   10-K405                     Documents   
2000-12-14      10-K                     Documents   
1999-12-22      10-K                     Documents   
1998-12-23   10-K405                     Documents   
1998-01-23    10-K/A                     Documents   
1997-12-05      10-K                     Documents   
1996-12-19      10-K                     Documents   
1995-12-19      10-K                     Documents   
1994-12-13      10-K                     Documents   

                                                   Description  \
Filing Date                                                      
2020-10-30   Annual report [Section 13 and 15(d), not S-K I...   
2019-10-31   Annual report [Section 13 and 15(d), not S-K I...   
2018-11-05   Annual report [Section 13 and 15(d), not S-K I...   
2017-11-03   Annual report [Section 13 and 15(d), not S-K I...   
2016-10-26   Annual report [Section 13 and 15(d), not S-K I...   
2015-10-28   Annual report [Section 13 and 15(d), not S-K I...   
2014-10-27   Annual report [Section 13 and 15(d), not S-K I...   
2013-10-30   Annual report [Section 13 and 15(d), not S-K I...   
2012-10-31   Annual report [Section 13 and 15(d), not S-K I...   
2011-10-26   Annual report [Section 13 and 15(d), not S-K I...   
2010-10-27   Annual report [Section 13 and 15(d), not S-K I...   
2010-01-25   [Amend] Annual report [Section 13 and 15(d), n...   
2009-10-27   Annual report [Section 13 and 15(d), not S-K I...   
2008-11-05   Annual report [Section 13 and 15(d), not S-K I...   
2007-11-15   Annual report [Section 13 and 15(d), not S-K I...   
2006-12-29   Annual report [Section 13 and 15(d), not S-K I...   
2005-12-01   Annual report [Section 13 and 15(d), not S-K I...   
2004-12-03   Annual report [Section 13 and 15(d), not S-K I...   
2003-12-19   Annual report [Section 13 and 15(d), not S-K I...   
2002-12-19   Annual report [Section 13 and 15(d), not S-K I...   
2001-12-21   Annual report [Sections 13 and 15(d), S-K Item...   
2000-12-14   Annual report [Section 13 and 15(d), not S-K I...   
1999-12-22   Annual report [Section 13 and 15(d), not S-K I...   
1998-12-23   Annual report [Sections 13 and 15(d), S-K Item...   
1998-01-23   [Amend] Annual report [Section 13 and 15(d), n...   
1997-12-05   Annual report [Section 13 and 15(d), not S-K I...   
1996-12-19   Annual report [Section 13 and 15(d), not S-K I...   
1995-12-19   Annual report [Section 13 and 15(d), not S-K I...   
1994-12-13   Annual report [Section 13 and 15(d), not S-K I...   

               File/Film Number  \
Filing Date                       
2020-10-30   001-36743201273977   
2019-10-31   001-36743191181423   
2018-11-05   001-36743181158788   
2017-11-03   001-36743171174673   
2016-10-26   001-36743161953070   
2015-10-28   001-36743151180619   
2014-10-27 

In [230]:
self.data_files

Getting data files...


Filings                        Format  \
Filing Date                                          
2020-10-30      10-K  Documents   Interactive Data   
2019-10-31      10-K  Documents   Interactive Data   
2018-11-05      10-K  Documents   Interactive Data   
2017-11-03      10-K  Documents   Interactive Data   
2016-10-26      10-K  Documents   Interactive Data   
2015-10-28      10-K  Documents   Interactive Data   
2014-10-27      10-K  Documents   Interactive Data   
2013-10-30      10-K  Documents   Interactive Data   
2012-10-31      10-K  Documents   Interactive Data   
2011-10-26      10-K  Documents   Interactive Data   
2010-10-27      10-K  Documents   Interactive Data   
2010-01-25    10-K/A  Documents   Interactive Data   
2009-10-27      10-K  Documents   Interactive Data   
2008-11-05      10-K                     Documents   
2007-11-15      10-K                     Documents   
2006-12-29      10-K                     Documents   
2005-12-01      10-K                     Documents   
2004-12-03      10-K                     Documents   
2003-12-19      10-K                     Documents   
2002-12-19      10-K                     Documents   
2001-12-21   10-K405                     Documents   
2000-12-14      10-K                     Documents   
1999-12-22      10-K                     Documents   
1998-12-23   10-K405                     Documents   
1998-01-23    10-K/A                     Documents   
1997-12-05      10-K                     Documents   
1996-12-19      10-K                     Documents   
1995-12-19      10-K                     Documents   
1994-12-13      10-K                     Documents   

                                                   Description  \
Filing Date                                                      
2020-10-30   Annual report [Section 13 and 15(d), not S-K I...   
2019-10-31   Annual report [Section 13 and 15(d), not S-K I...   
2018-11-05   Annual report [Section 13 and 15(d), not S-K I...   
2017-11-03   Annual report [Section 13 and 15(d), not S-K I...   
2016-10-26   Annual report [Section 13 and 15(d), not S-K I...   
2015-10-28   Annual report [Section 13 and 15(d), not S-K I...   
2014-10-27   Annual report [Section 13 and 15(d), not S-K I...   
2013-10-30   Annual report [Section 13 and 15(d), not S-K I...   
2012-10-31   Annual report [Section 13 and 15(d), not S-K I...   
2011-10-26   Annual report [Section 13 and 15(d), not S-K I...   
2010-10-27   Annual report [Section 13 and 15(d), not S-K I...   
2010-01-25   [Amend] Annual report [Section 13 and 15(d), n...   
2009-10-27   Annual report [Section 13 and 15(d), not S-K I...   
2008-11-05   Annual report [Section 13 and 15(d), not S-K I...   
2007-11-15   Annual report [Section 13 and 15(d), not S-K I...   
2006-12-29   Annual report [Section 13 and 15(d), not S-K I...   
2005-12-01   Annual report [Section 13 and 15(d), not S-K I...   
2004-12-03   Annual report [Section 13 and 15(d), not S-K I...   
2003-12-19   Annual report [Section 13 and 15(d), not S-K I...   
2002-12-19   Annual report [Section 13 and 15(d), not S-K I...   
2001-12-21   Annual report [Sections 13 and 15(d), S-K Item...   
2000-12-14   Annual report [Section 13 and 15(d), not S-K I...   
1999-12-22   Annual report [Section 13 and 15(d), not S-K I...   
1998-12-23   Annual report [Sections 13 and 15(d), S-K Item...   
1998-01-23   [Amend] Annual report [Section 13 and 15(d), n...   
1997-12-05   Annual report [Section 13 and 15(d), not S-K I...   
1996-12-19   Annual report [Section 13 and 15(d), not S-K I...   
1995-12-19   Annual report [Section 13 and 15(d), not S-K I...   
1994-12-13   Annual report [Section 13 and 15(d), not S-K I...   

               File/Film Number  \
Filing Date                       
2020-10-30   001-36743201273977   
2019-10-31   001-36743191181423   
2018-11-05   001-36743181158788   
2017-11-03   001-36743171174673   
2016-10-26   001-36743161953070   
2015-10-28   001-36743151180619   
2014-10-27 

In [283]:
# data

instance_url = self.data_files.iloc[0]['INS']

resp = requests.get(instance_url, headers=self._request_headers)
root = ET.fromstring(resp.content)

# get namespace from root tag
namespace = root.tag.split('}')[0] + '}'

res = {}
for child in root.iter():
    
    if 'us-gaap' in child.tag and child.attrib:
        
        namespace, tag = child.tag.split('}')
        
        namespace += '}'
        
        context = child.attrib['contextRef']
        period = context.split('_')[-1]
        
        if tag not in res:
            res[tag] = {}
            
        val = child.text
        try:
            val = float(val)
        except:
            pass
        
        res[tag][period] = val
                                  

In [284]:
# calculation

cal_link = self.data_files.iloc[0]['CAL']
resp = requests.get(cal_link, headers=self._request_headers)

root = ET.fromstring(resp.content)

# get namespace from root tag
namespace = root.tag.split('}')[0] + '}'

# results
arcs = {}
parents = set()
children = set()


# find calculation arcs
for calc_arc in root.findall(f'.//{namespace}calculationArc'):

#     # attribute with cleaned names
    attrib = {}
    for key in calc_arc.keys():

        # remove xlink namespace
        newkey = key.split('}')[-1]

        # reassign to
        attrib[newkey] = calc_arc.attrib[key]

    parent_name = attrib['from'].split('_')[-2]
    child_name = attrib['to'].split('_')[-2]
    
    
    if parent_name not in arcs:
        arcs[parent_name] = {'values' : res[parent_name] if parent_name in res else None,
                             'children' : {}
                       }
    
    arcs[parent_name]['children'][child_name] = {'order' : int(attrib['order']),
                                                 'weight' : float(attrib['weight'])}
    
    if child_name in res:
        arcs[parent_name]['children'][child_name].update(res[child_name])
    
    parents.add(parent_name)
    children.add(child_name)
    
parents - children

{'Assets',
 'AvailableForSaleDebtSecuritiesAmortizedCostBasis',
 'CashCashEquivalentsRestrictedCashAndRestrictedCashEquivalents',
 'CashCashEquivalentsRestrictedCashAndRestrictedCashEquivalentsPeriodIncreaseDecreaseIncludingExchangeRateEffect',
 'ComprehensiveIncomeNetOfTax',
 'DebtInstrumentCarryingAmount',
 'DeferredTaxAssetsLiabilitiesNet',
 'LesseeOperatingandFinanceLeaseLiabilityPaymentsDue',
 'LiabilitiesAndStockholdersEquity',
 'OperatingandFinanceLeaseRightofUseAsset',
 'UnrecordedUnconditionalPurchaseObligationBalanceSheetAmount',
 'WeightedAverageNumberOfDilutedSharesOutstanding'}

In [296]:
arcs[lineitem]

{'values': {'D20190929-20200926': 104956000000.0,
  'D20180930-20190928': 98392000000.0,
  'D20171001-20180929': 101839000000.0,
  'D20200628-20200926': 24689000000.0,
  'D20200329-20200627': 22680000000.0,
  'D20191229-20200328': 22370000000.0,
  'D20190929-20191228': 35217000000.0,
  'D20190630-20190928': 24313000000.0,
  'D20190331-20190629': 20227000000.0,
  'D20181230-20190330': 21821000000.0,
  'D20180930-20181229': 32031000000.0},
 'children': {'RevenueFromContractWithCustomerExcludingAssessedTax': {'order': 1,
   'weight': 1.0,
   'D20190929-20200926': 274515000000.0,
   'D20180930-20190928': 260174000000.0,
   'D20171001-20180929': 265595000000.0,
   'D20200628-20200926': 64698000000.0,
   'D20200329-20200627': 59685000000.0,
   'D20191229-20200328': 58313000000.0,
   'D20190929-20191228': 91819000000.0,
   'D20190630-20190928': 64040000000.0,
   'D20190331-20190629': 53809000000.0,
   'D20181230-20190330': 58015000000.0,
   'D20180930-20181229': 84310000000.0},
  'CostOfGoods

In [285]:
lineitem = 'GrossProfit'
df = pd.DataFrame(arcs[lineitem]['children']).T.fillna(0)

In [295]:
df

order  weight  \
RevenueFromContractWithCustomerExcludingAssesse...    1.0     1.0   
CostOfGoodsAndServicesSold                            2.0    -1.0   

                                                    D20190929-20200926  \
RevenueFromContractWithCustomerExcludingAssesse...        2.745150e+11   
CostOfGoodsAndServicesSold                               -5.840000e+08   

                                                    D20180930-20190928  \
RevenueFromContractWithCustomerExcludingAssesse...        2.601740e+11   
CostOfGoodsAndServicesSold                               -4.820000e+08   

                                                    D20171001-20180929  \
RevenueFromContractWithCustomerExcludingAssesse...        2.655950e+11   
CostOfGoodsAndServicesSold                                1.637560e+11   

                                                    D20200628-20200926  \
RevenueFromContractWithCustomerExcludingAssesse...        6.469800e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20200329-20200627  \
RevenueFromContractWithCustomerExcludingAssesse...        5.968500e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20191229-20200328  \
RevenueFromContractWithCustomerExcludingAssesse...        5.831300e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20190929-20191228  \
RevenueFromContractWithCustomerExcludingAssesse...        9.181900e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20190630-20190928  \
RevenueFromContractWithCustomerExcludingAssesse...        6.404000e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20190331-20190629  \
RevenueFromContractWithCustomerExcludingAssesse...        5.380900e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20181230-20190330  \
RevenueFromContractWithCustomerExcludingAssesse...        5.801500e+10   
CostOfGoodsAndServicesSold                                0.000000e+00   

                                                    D20180930-20181229  
RevenueFromContractWithCustomerExcludingAssesse...        8.431000e+10  
CostOfGoodsAndServicesSold                                0.000000e+00

In [292]:
arcs[lineitem]['values']

{'D20190929-20200926': 104956000000.0,
 'D20180930-20190928': 98392000000.0,
 'D20171001-20180929': 101839000000.0,
 'D20200628-20200926': 24689000000.0,
 'D20200329-20200627': 22680000000.0,
 'D20191229-20200328': 22370000000.0,
 'D20190929-20191228': 35217000000.0,
 'D20190630-20190928': 24313000000.0,
 'D20190331-20190629': 20227000000.0,
 'D20181230-20190330': 21821000000.0,
 'D20180930-20181229': 32031000000.0}

In [294]:
df.mul(df['weight'], axis=0).sum()

order                -1.000000e+00
weight                2.000000e+00
D20190929-20200926    2.750990e+11
D20180930-20190928    2.606560e+11
D20171001-20180929    1.018390e+11
D20200628-20200926    6.469800e+10
D20200329-20200627    5.968500e+10
D20191229-20200328    5.831300e+10
D20190929-20191228    9.181900e+10
D20190630-20190928    6.404000e+10
D20190331-20190629    5.380900e+10
D20181230-20190330    5.801500e+10
D20180930-20181229    8.431000e+10
dtype: float64

In [ ]:


def clean_fs(self, df):
    '''
    Clean financial statement

    TODO:
        * identify statements from file keys
        * identify column names in data
    '''

    name, denom = df.columns[0].split('-')

    # clean index
    df = df.set_index(df.columns[0]) # set index
    df.index = df.index.str.replace('$', '\$', regex=False) # replace dollar signs
    df.index = df.index.str.lower().str.strip()


    # columns to date time
    if all(df.dtypes == float):
        df.columns = pd.to_datetime(df.columns)
    else:
        df.columns = pd.to_datetime(df.iloc[0])
        df = df.iloc[1:]

    df.columns.name = ''

    # rename index
    df.index.name = name.strip() # + ' (Millions USD)'

    # # denominate in millions
    d = denom.split()[-1].lower()

    # denominate in millions
    if d in self._denom_key:
        denom_mult = self._denom_key[d]
        df = df * denom_mult
        df.index.name += ' (Millions USD)'

    return df

In [35]:
self = Edgar('fb')

In [36]:
self

<SEC Edgar 10-K 0001326801 [fb][Facebook Inc]>

In [23]:
resp = requests.get(self._cik_url)
self._query_doc = html.fromstring(resp.content)

# get company info
company_el = self._query_doc.xpath('//span[@class="companyName"]')

In [7]:
sample = np.random.choice(scn.index)
# sample = 'AAPL'
print(scn.loc[sample], '\n')

self = Edgar(sample)

# print(self.company_name, self.cik)
print(f'{self.filing} documents found:', len(self.documents))
print(self)

Name                 Sichuan Expressway Company Limited
Price (Intraday)                                   0.23
Change                                            -0.01
% Change                                          -0.07
Volume                                              600
Avg Vol (3 month)                                 454.0
Market Cap                                       1.168B
PE Ratio (TTM)                                      NaN
52 Week Range                                          
mktcap                                     1168000000.0
Name: SEXHF, dtype: object 

10-K documents found: 0
<SEC Edgar 10-K  [SEXHF][]>


excel_urls = self._get_excel_urls()
stmts = {}

for index, url in zip(excel_urls.index, excel_urls):
    
    print(index)
    
    try:
        
        # read file
        files = pd.read_excel(url, sheet_name=None)
        keys = list(files.keys())

        for k in keys:
            try:
                
                # clean file
                df = clean_fs(files[k])
                
                # get statement name
                stmt_name = df.index.name
                
                # add to dict
                if stmt_name not in stmts:
                    stmts[stmt_name] = []
                    
                stmts[stmt_name].append(df)
                
            except:
                pass
    except:
        print('\t> not available')
        pass

# Scrape XBRL data

In [140]:
from pprint import pprint

import csv
import pathlib
import collections
import xml.etree.ElementTree as ET

In [ ]:
self = Edgar('fb', '10-Q')
print(self.documents['url'][0])

In [49]:
# get document url from SEC Edgar
# for doc url in self.docs['docs_url']:
doc_url =  self.documents['url'][0]

# get text file data
doc = html.fromstring(requests.get(doc_url).content)

print(doc_url)

https://sec.gov/Archives/edgar/data/1326801/000132680120000084/0001326801-20-000084-index.htm


In [80]:
# storage components
storage_list = []
storage_values = {}
storage_gaap = {}

# create named tuple
FilingTuple = collections.namedtuple('FilingTuple', ['file_path', 'namespace_root', 'namespace_label'])

# categories
avoids = ['linkbase', 'roleRef']
parse = ['label', 'labelLink', 'labelArc', 'loc', 'definition', 'definitionArc']

# sets for keys
lab_set = set()
cal_set = set()

In [98]:
# XML file types
file_types = {
#     'instance':'htm',
    
    'calculation':'cal',
    'definition':'def',
    'label':'lab'}

# initialize list of named tuples
file_list = []

# list of named tuple for files
for k, v in file_types.items():
    
    href = doc.xpath(f'//a[contains(@href, "{v}.xml")]')[0].get('href')
    url = self._base + href
    
    print(url)
    
    file_list.append(
        FilingTuple(url, r'{http://www.xbrl.org/2003/linkbase}' + f'{k}Link', k)
    )
    

for file in file_list:

    # read file
    resp = requests.get(file.file_path)
    tree = ET.fromstring(resp.content)

    # print(tree)

    elements = tree.findall(file.namespace_root)

    for element in elements:

        # if element has children, want to parse as well
        for child in element.iter():

            namespace, label = child.tag.split('}')

            if label in parse:    

                # define item type
                element_label = file.namespace_label + '_' + label

                storage = {}
                storage['item_type'] = element_label

                cal_keys = child.keys()

                for key in cal_keys:

                    if '}' in key:
                        new_key = key.split('}')[1]
                        storage[new_key] = child.attrib[key]

                    else:
                        storage[key] = child.attrib[key]


                if element_label == 'label_label':

                    # grab label key
                    key_store = storage['label']

                    # create master key
                    master_key = key_store.replace('lab_', '')

                    # split master key
                    label_split = master_key.split('_')
                    
                    # create gaap id
                    gaap_id = label_split[0] + ':' + label_split[1]
                    
                    storage_values[master_key] = {
                        'label_id' : key_store,
                        'location_id' : key_store.replace('lab_', 'loc_'),
                        'us_gaap_id' : gaap_id,
                        'us_gaap_value' : None,
                        element_label : storage,
                    }
                    
                    storage_gaap[gaap_id] = {
                        'id' : gaap_id,
                        'master_id' : master_key
                    }
                
                storage_list.append([file.namespace_label, storage])

https://sec.gov/Archives/edgar/data/1326801/000132680120000084/fb-20200930_cal.xml
https://sec.gov/Archives/edgar/data/1326801/000132680120000084/fb-20200930_def.xml
https://sec.gov/Archives/edgar/data/1326801/000132680120000084/fb-20200930_lab.xml


In [143]:
pprint(storage_values)

{'country_US_9882607C1A5F2417E2567A4747CFCAEB': {'label_id': 'lab_country_US_9882607C1A5F2417E2567A4747CFCAEB',
                                                 'label_label': {'id': 'lab_country_US_9882607C1A5F2417E2567A4747CFCAEB_label_en-US',
                                                                 'item_type': 'label_label',
                                                                 'label': 'lab_country_US_9882607C1A5F2417E2567A4747CFCAEB',
                                                                 'lang': 'en-US',
                                                                 'role': 'http://www.xbrl.org/2003/role/label',
                                                                 'type': 'resource'},
                                                 'location_id': 'loc_country_US_9882607C1A5F2417E2567A4747CFCAEB',
                                                 'us_gaap_id': 'country:US',
                                                 'us_gaap_value'

 'us-gaap_AllocatedShareBasedCompensationExpense_2995427CD1C9337B35E47A474733EB70': {'label_id': 'lab_us-gaap_AllocatedShareBasedCompensationExpense_2995427CD1C9337B35E47A474733EB70',
                                                                                     'label_label': {'id': 'lab_us-gaap_AllocatedShareBasedCompensationExpense_2995427CD1C9337B35E47A474733EB70_label_en-US',
                                                                                                     'item_type': 'label_label',
                                                                                                     'label': 'lab_us-gaap_AllocatedShareBasedCompensationExpense_2995427CD1C9337B35E47A474733EB70',
                                                                                                     'lang': 'en-US',
                                                                                                     'role': 'http://www.xbrl.org/2003/role/label',
                  

                                                                               'us_gaap_value': None},
 'us-gaap_FinanceLeaseLiabilityPaymentsRemainderOfFiscalYear_AAFED4B8474EE266130B7A47485C2905': {'label_id': 'lab_us-gaap_FinanceLeaseLiabilityPaymentsRemainderOfFiscalYear_AAFED4B8474EE266130B7A47485C2905',
                                                                                                 'label_label': {'id': 'lab_us-gaap_FinanceLeaseLiabilityPaymentsRemainderOfFiscalYear_AAFED4B8474EE266130B7A47485C2905_label_en-US',
                                                                                                                 'item_type': 'label_label',
                                                                                                                 'label': 'lab_us-gaap_FinanceLeaseLiabilityPaymentsRemainderOfFiscalYear_AAFED4B8474EE266130B7A47485C2905',
                                                                                                 

 'us-gaap_NoncurrentAssets_2AF5CCE6D0890CF34D6D7A474752B914': {'label_id': 'lab_us-gaap_NoncurrentAssets_2AF5CCE6D0890CF34D6D7A474752B914',
                                                               'label_label': {'id': 'lab_us-gaap_NoncurrentAssets_2AF5CCE6D0890CF34D6D7A474752B914_label_en-US',
                                                                               'item_type': 'label_label',
                                                                               'label': 'lab_us-gaap_NoncurrentAssets_2AF5CCE6D0890CF34D6D7A474752B914',
                                                                               'lang': 'en-US',
                                                                               'role': 'http://www.xbrl.org/2003/role/label',
                                                                               'type': 'resource'},
                                                               'location_id': 'loc_us-gaap_NoncurrentAssets_2AF5CCE6

                                                                                                                                                                                                        'type': 'resource'},
                                                                                                                                                                                        'location_id': 'loc_us-gaap_ShareBasedCompensationArrangementByShareBasedPaymentAwardEquityInstrumentsOtherThanOptionsVestedInPeriodWeightedAverageGrantDateFairValue_85432E3759FF2D5F911A7A47487B06B7',
                                                                                                                                                                                        'us_gaap_id': 'us-gaap:ShareBasedCompensationArrangementByShareBasedPaymentAwardEquityInstrumentsOtherThanOptionsVestedInPeriodWeightedAverageGrantDateFairValue',
                                               

In [144]:
pprint(storage_list)

[['calculation',
  {'href': 'fb-20200930.xsd#fb_CashCashEquivalentsAndMarketableSecuritiesAtCarryingValue',
   'item_type': 'calculation_loc',
   'label': 'loc_fb_CashCashEquivalentsAndMarketableSecuritiesAtCarryingValue_7ed714d4-6324-488a-f34c-7a4719f4c126',
   'type': 'locator'}],
 ['calculation',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_CashAndCashEquivalentsAtCarryingValue',
   'item_type': 'calculation_loc',
   'label': 'loc_us-gaap_CashAndCashEquivalentsAtCarryingValue_26247a2d-7bac-8834-3dc5-06c993b10b2c',
   'type': 'locator'}],
 ['calculation',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_AvailableForSaleSecuritiesDebtSecuritiesCurrent',
   'item_type': 'calculation_loc',
   'label': 'loc_us-gaap_AvailableForSaleSecuritiesDebtSecuritiesCurrent_b49a072d-9bbd-fc1a-97d6-c98455d056b7',
   'type': 'locator'}],
 ['calculation',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-ga

 ['definition',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_BalanceSheetLocationDomain',
   'item_type': 'definition_loc',
   'label': 'loc_us-gaap_BalanceSheetLocationDomain_A37C5FC755BC7F6FEF264D4B998A1725',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://xbrl.org/int/dim/arcrole/dimension-domain',
   'from': 'loc_us-gaap_BalanceSheetLocationAxis_13A3D6CF25B093B18CEE4D4B9989645A',
   'item_type': 'definition_definitionArc',
   'order': '1',
   'to': 'loc_us-gaap_BalanceSheetLocationDomain_A37C5FC755BC7F6FEF264D4B998A1725',
   'type': 'arc'}],
 ['definition',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_PrepaidExpensesAndOtherCurrentAssetsMember',
   'item_type': 'definition_loc',
   'label': 'loc_us-gaap_PrepaidExpensesAndOtherCurrentAssetsMember_6CC4B14F46F6636501A54D4B998AE550',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://xbrl.org/int/dim/arcrole/domain-member',
   'from': 'lo

  {'href': 'https://xbrl.sec.gov/dei/2020/dei-2020-01-31.xsd#dei_CityAreaCode',
   'item_type': 'definition_loc',
   'label': 'loc_dei_CityAreaCode_13210F47D3440567D3FE7A4747B0CF48',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://xbrl.org/int/dim/arcrole/domain-member',
   'from': 'loc_dei_EntityInformationLineItems_DDB6C7E5F0DA955486877A4747B02428',
   'item_type': 'definition_definitionArc',
   'order': '13',
   'to': 'loc_dei_CityAreaCode_13210F47D3440567D3FE7A4747B0CF48',
   'type': 'arc'}],
 ['definition',
  {'href': 'https://xbrl.sec.gov/dei/2020/dei-2020-01-31.xsd#dei_LocalPhoneNumber',
   'item_type': 'definition_loc',
   'label': 'loc_dei_LocalPhoneNumber_45818B2F3D11CBD90A717A4747C08FD6',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://xbrl.org/int/dim/arcrole/domain-member',
   'from': 'loc_dei_EntityInformationLineItems_DDB6C7E5F0DA955486877A4747B02428',
   'item_type': 'definition_definitionArc',
   'order': '14',
   'to': 'loc_dei_LocalPhoneNu

 ['definition',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_FiniteLivedIntangibleAssetsAccumulatedAmortization',
   'item_type': 'definition_loc',
   'label': 'loc_us-gaap_FiniteLivedIntangibleAssetsAccumulatedAmortization_4B43FB85FB4D6E6B79717A47482D2BDC',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://xbrl.org/int/dim/arcrole/domain-member',
   'from': 'loc_us-gaap_FiniteLivedIntangibleAssetsLineItems_4C8F8979163FF01E6A617A47482D017D',
   'item_type': 'definition_definitionArc',
   'order': '3',
   'to': 'loc_us-gaap_FiniteLivedIntangibleAssetsAccumulatedAmortization_4B43FB85FB4D6E6B79717A47482D2BDC',
   'type': 'arc'}],
 ['definition',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_FiniteLivedIntangibleAssetsNet',
   'item_type': 'definition_loc',
   'label': 'loc_us-gaap_FiniteLivedIntangibleAssetsNet_4CE5B85910B87F364A687A47482DB108',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http:

 ['definition',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_CommonStockCapitalSharesReservedForFutureIssuance',
   'item_type': 'definition_loc',
   'label': 'loc_us-gaap_CommonStockCapitalSharesReservedForFutureIssuance_55A3CCDBDCD9E312D6497A4747C00208',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://xbrl.org/int/dim/arcrole/domain-member',
   'from': 'loc_us-gaap_ShareBasedCompensationArrangementByShareBasedPaymentAwardLineItems_1CD01A64C03847EA0D3B7A4747C053B1',
   'item_type': 'definition_definitionArc',
   'order': '3',
   'to': 'loc_us-gaap_CommonStockCapitalSharesReservedForFutureIssuance_55A3CCDBDCD9E312D6497A4747C00208',
   'type': 'arc'}],
 ['definition',
  {'href': 'fb-20200930.xsd#fb_SharesReservedForIssuanceIncreasePercentage',
   'item_type': 'definition_loc',
   'label': 'loc_fb_SharesReservedForIssuanceIncreasePercentage_791581F147D88894E38B7A4747C0F8CB',
   'type': 'locator'}],
 ['definition',
  {'arcrole': 'http://x

...

 ['label',
  {'arcrole': 'http://www.xbrl.org/2003/arcrole/concept-label',
   'from': 'loc_srt_LitigationCaseTypeDomain_0F85BC9B57C9E7D28D5E4D4B98AC8186',
   'item_type': 'label_labelArc',
   'order': '1',
   'to': 'lab_srt_LitigationCaseTypeDomain_0F85BC9B57C9E7D28D5E4D4B98AC8186',
   'type': 'arc'}],
 ['label',
  {'id': 'lab_fb_AlteraCorpVCommissionerMember_4EA4714DED5C9B6F32554D4B98ACF8D3_terseLabel_en-US',
   'item_type': 'label_label',
   'label': 'lab_fb_AlteraCorpVCommissionerMember_4EA4714DED5C9B6F32554D4B98ACF8D3',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/role/terseLabel',
   'type': 'resource'}],
 ['label',
  {'id': 'lab_fb_AlteraCorpVCommissionerMember_4EA4714DED5C9B6F32554D4B98ACF8D3_label_en-US',
   'item_type': 'label_label',
   'label': 'lab_fb_AlteraCorpVCommissionerMember_4EA4714DED5C9B6F32554D4B98ACF8D3',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/role/label',
   'type': 'resource'}],
 ['label',
  {'id': 'lab_fb_AlteraCorpVCommissionerMem

  {'id': 'lab_dei_EntityRegistrantName_111A0756418EEA5AE0797A4747B0A8CA_label_en-US',
   'item_type': 'label_label',
   'label': 'lab_dei_EntityRegistrantName_111A0756418EEA5AE0797A4747B0A8CA',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/role/label',
   'type': 'resource'}],
 ['label',
  {'href': 'https://xbrl.sec.gov/dei/2020/dei-2020-01-31.xsd#dei_EntityRegistrantName',
   'item_type': 'label_loc',
   'label': 'loc_dei_EntityRegistrantName_111A0756418EEA5AE0797A4747B0A8CA',
   'type': 'locator'}],
 ['label',
  {'arcrole': 'http://www.xbrl.org/2003/arcrole/concept-label',
   'from': 'loc_dei_EntityRegistrantName_111A0756418EEA5AE0797A4747B0A8CA',
   'item_type': 'label_labelArc',
   'order': '1',
   'to': 'lab_dei_EntityRegistrantName_111A0756418EEA5AE0797A4747B0A8CA',
   'type': 'arc'}],
 ['label',
  {'id': 'lab_dei_EntityIncorporationStateCountryCode_400C824CA5D8FFAC3E017A4747B01F15_terseLabel_en-US',
   'item_type': 'label_label',
   'label': 'lab_dei_EntityIncorporati

   'type': 'arc'}],
 ['label',
  {'id': 'lab_fb_ShareBasedCompensationArrangementByShareBasedPaymentAwardEquityInstrumentsOtherThanOptionsRollforwardAbstract_89E2ECAB9B9CB561D8DD7A47487B99F6_terseLabel_en-US',
   'item_type': 'label_label',
   'label': 'lab_fb_ShareBasedCompensationArrangementByShareBasedPaymentAwardEquityInstrumentsOtherThanOptionsRollforwardAbstract_89E2ECAB9B9CB561D8DD7A47487B99F6',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/role/terseLabel',
   'type': 'resource'}],
 ['label',
  {'id': 'lab_fb_ShareBasedCompensationArrangementByShareBasedPaymentAwardEquityInstrumentsOtherThanOptionsRollforwardAbstract_89E2ECAB9B9CB561D8DD7A47487B99F6_label_en-US',
   'item_type': 'label_label',
   'label': 'lab_fb_ShareBasedCompensationArrangementByShareBasedPaymentAwardEquityInstrumentsOtherThanOptionsRollforwardAbstract_89E2ECAB9B9CB561D8DD7A47487B99F6',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/role/label',
   'type': 'resource'}],
 ['label',
  {'id'

   'type': 'resource'}],
 ['label',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_FiniteLivedIntangibleAssetsByMajorClassAxis',
   'item_type': 'label_loc',
   'label': 'loc_us-gaap_FiniteLivedIntangibleAssetsByMajorClassAxis_EC5DCE82188B04463FEF7A47482D5837',
   'type': 'locator'}],
 ['label',
  {'arcrole': 'http://www.xbrl.org/2003/arcrole/concept-label',
   'from': 'loc_us-gaap_FiniteLivedIntangibleAssetsByMajorClassAxis_EC5DCE82188B04463FEF7A47482D5837',
   'item_type': 'label_labelArc',
   'order': '1',
   'to': 'lab_us-gaap_FiniteLivedIntangibleAssetsByMajorClassAxis_EC5DCE82188B04463FEF7A47482D5837',
   'type': 'arc'}],
 ['label',
  {'id': 'lab_us-gaap_FiniteLivedIntangibleAssetsMajorClassNameDomain_CDA8CFE1F21DBA9306597A47482DC742_terseLabel_en-US',
   'item_type': 'label_label',
   'label': 'lab_us-gaap_FiniteLivedIntangibleAssetsMajorClassNameDomain_CDA8CFE1F21DBA9306597A47482DC742',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/

   'type': 'resource'}],
 ['label',
  {'id': 'lab_us-gaap_CommonStockSharesIssued_4510109C79287DDE92B47A474772F8FC_label_en-US',
   'item_type': 'label_label',
   'label': 'lab_us-gaap_CommonStockSharesIssued_4510109C79287DDE92B47A474772F8FC',
   'lang': 'en-US',
   'role': 'http://www.xbrl.org/2003/role/label',
   'type': 'resource'}],
 ['label',
  {'href': 'http://xbrl.fasb.org/us-gaap/2020/elts/us-gaap-2020-01-31.xsd#us-gaap_CommonStockSharesIssued',
   'item_type': 'label_loc',
   'label': 'loc_us-gaap_CommonStockSharesIssued_4510109C79287DDE92B47A474772F8FC',
   'type': 'locator'}],
 ['label',
  {'arcrole': 'http://www.xbrl.org/2003/arcrole/concept-label',
   'from': 'loc_us-gaap_CommonStockSharesIssued_4510109C79287DDE92B47A474772F8FC',
   'item_type': 'label_labelArc',
   'order': '1',
   'to': 'lab_us-gaap_CommonStockSharesIssued_4510109C79287DDE92B47A474772F8FC',
   'type': 'arc'}],
 ['label',
  {'id': 'lab_us-gaap_CommonStockSharesOutstanding_4CA26B3FC58E9AFDB24C7A4747728CC3_

In [142]:
pprint(storage_gaap)

{'country:US': {'id': 'country:US',
                'master_id': 'country_US_9882607C1A5F2417E2567A4747CFCAEB'},
 'dei:AmendmentFlag': {'id': 'dei:AmendmentFlag',
                       'master_id': 'dei_AmendmentFlag_D88667186A7447F68AF27A4747C075AD'},
 'dei:CityAreaCode': {'id': 'dei:CityAreaCode',
                      'master_id': 'dei_CityAreaCode_13210F47D3440567D3FE7A4747B0CF48'},
 'dei:CoverAbstract': {'id': 'dei:CoverAbstract',
                       'master_id': 'dei_CoverAbstract_E5B8C07B02DADFD4B64B7A4747B02456'},
 'dei:CurrentFiscalYearEndDate': {'id': 'dei:CurrentFiscalYearEndDate',
                                  'master_id': 'dei_CurrentFiscalYearEndDate_438041B7D631A4C301567A4747C0921E'},
 'dei:DocumentFiscalPeriodFocus': {'id': 'dei:DocumentFiscalPeriodFocus',
                                   'master_id': 'dei_DocumentFiscalPeriodFocus_CC7CCB6D8FE3D638011A7A4747C0DD3E'},
 'dei:DocumentFiscalYearFocus': {'id': 'dei:DocumentFiscalYearFocus',
                        

# Parse text file

In [89]:


# for doc url in self.docs['docs_url']:
doc_url =  self.docs['docs_url'][0]

# get text file data
doc = html.fromstring(requests.get(doc_url).content)
href = doc.xpath('//a[contains(text(),".txt")]')[0].get('href')

# get url for txt file
url =  self._base + href
data = requests.get(url).content
print(url)

# parse with beautiful soup
soup = BeautifulSoup(data, 'lxml')

sec_header = soup.find('sec-header')

https://sec.gov/Archives/edgar/data/1041514/000106299320004444/0001062993-20-004444.txt


In [94]:
for i, td in enumerate(soup.find_all('td')):
    
    print(i, td.text.strip())

0 For the transition period from
1 
2 To
3 
4 Florida
5 98-0171860
6 (State or other jurisdiction
7 (IRS Employer
8 of incorporation or organization)
9 Identification No.)
10 President Place, 4th Floor, Cnr. Jan Smuts Avenue and Bolton Road
11 Rosebank, Johannesburg 2196, South Africa
12 (Address of principal executive offices, including zip code)
13 Title of each class
14 Trading Symbol(s)
15 Name of each exchange
on which registered
16 Common stock, par value $0.001 per share
17 UEPS
18 NASDAQ Global Select Market
19 [   ]
20 Large accelerated filer
21 [X]
22 Accelerated filer
23 
24 
25 
26 
27 [   ]
28 Non-accelerated filer
29 [X]
30 Smaller reporting company
31 
32 
33 
34 
35 
36 
37 [   ]
38 Emerging growth company
39 
40 
41 
42 
43 
44 
45 Page
46 PART I
47 
48 Item 1.
49 Business
50 2
51 Item 1A.
52 Risk Factors
53 8
54 Item 1B.
55 Unresolved Staff Comments
56 25
57 Item 2.
58 Properties
59 25
60 Item 3.
61 Legal Proceedings
62 25
63 Item 4.
64 Mine Safety Disclosures
65 27
6

1579 nm
1580 Bank Frick
1581 (17,273)
1582 
1583 (1,542)
1584 
1585 1,020%
1586 Share of net income
1587 1,421
1588 
1589 1,109
1590 
1591 28%
1592 Amortization of intangible assets, net of deferred tax
1593 (433)
1594 
1595 (567)
1596 
1597 (24%)
1598 Impairment
1599 (18,261)
1600 
1601 -
1602 
1603 nm
1604 Other
1605 -
1606 
1607 (2,084)
1608 
1609 nm
1610 Finbond
1611 1,840
1612 
1613 2,619
1614 
1615 (30%)
1616 Other
1617 (4,365)
1618 
1619 (684)
1620 
1621 538%
1622 Share of net loss
1623 (1,865)
1624 
1625 (684)
1626 
1627 173%
1628 Impairment
1629 (2,500)
1630 
1631 -
1632 
1633 nm
1634 Total (loss) earnings from equity-accounted investment
1635 (29,542)
1636 
1637 1,258
1638 
1639 nm
1640 
1641 
1642 
1643 
1644 
1645 
1646 
1647 
1648 
1649 
1650 Table 6
1651 In U.S. Dollars
1652 
1653 Year ended June 30,
1654 
1655 2020
1656 
1657 % of
1658 
1659 2019
1660 
1661 % of
1662 
1663 % change
1664 Operating Segment
1665 $ '000
1666 total
1667 $ '000
1668 total
1669 Revenue:
1670 
1

3247 -
3248 
3249 -
3250 
3251 nm
3252 Subtotal: Operating segments
3253 
3254 (609,193)
3255 
3256 36%
3257 
3258 1,087,843
3259 
3260 125%
3261 
3262 nm
3263 Corporate/eliminations
3264 
3265 (1,010,509)
3266 
3267 64%
3268 
3269 (339,480)
3270 
3271 (25%)
3272 
3273 198%
3274 Continuing
3275 
3276 (692,085)
3277 
3278 44%
3279 
3280 (176,513)
3281 
3282 (3%)
3283 
3284 292%
3285 Discontinued
3286 
3287 (318,424)
3288 
3289 20%
3290 
3291 (162,967)
3292 
3293 (22%)
3294 
3295 95%
3296 Consolidated operating (loss) income
3297 
3298 (1,619,702)
3299 
3300 100%
3301 
3302 748,363
3303 
3304 100%
3305 
3306 nm
3307 Continuing
3308 
3309 (1,925,412)
3310 
3311 119%
3312 
3313 683,110
3314 
3315 91%
3316 
3317 nm
3318 Discontinued
3319 
3320 305,710
3321 
3322 (19%)
3323 
3324 65,253
3325 
3326 9%
3327 
3328 368%
3329 Table 13
3330 Year ended June 30,
3331 
3332 2020
3333 
3334 2019
3335 
3336 2018
3337 
3338 2020
3339 
3340 2019
3341 
3342 2018
3343 $
3344 $
3345 $
3346 
3347 ZAR
3348 
3

5257 
5258 
5259 
5260 
5261 NET (LOSS) INCOME FROM CONTINUING OPERATIONS
5262 
5263 (97,214)
5264 
5265 
5266 (313,113)
5267 
5268 
5269 51,262
5270 
5271 
5272 
5273 
5274 
5275 
5276 
5277 
5278 
5279 
5280 NET INCOME FROM DISCONTINUED OPERATIONS (Note 3)
5281 
5282 6,402
5283 
5284 
5285 13,630
5286 
5287 
5288 9,945
5289 GAIN (LOSS) ON DISPOSAL OF DISCONTINUED OPERATION, net of tax (Note 3)
5290 
5291 12,454
5292 
5293 
5294 (9,175)
5295 
5296 
5297 -
5298 
5299 
5300 
5301 
5302 
5303 
5304 
5305 
5306 
5307 
5308 NET (LOSS) INCOME
5309 
5310 (78,358)
5311 
5312 
5313 (308,658)
5314 
5315 
5316 61,207
5317 
5318 
5319 
5320 
5321 
5322 
5323 
5324 
5325 
5326 
5327 LESS (ADD) NET INCOME (LOSS) ATTRIBUTABLE TO NON-CONTROLLING INTEREST
5328 
5329 -
5330 
5331 
5332 2,349
5333 
5334 
5335 (880)
5336 
5337 Continuing
5338 
5339 -
5340 
5341 
5342 (1,352)
5343 
5344 
5345 (880)
5346 
5347 Discontinued
5348 
5349 -
5350 
5351 
5352 3,701
5353 
5354 
5355 -
5356 
5357 
5358 
5359 
5360 

6828 
6829 
6830 
6831 
6832 
6833 
6834 
6835 568,000
6836 
6837 
6838 -
6839 
6840 
6841 
6842 
6843 
6844 
6845 
6846 
6847 -
6848 
6849 
6850 
6851 
6852 
6853 -
6854 
6855 
6856 
6857 
6858 Stock-based compensation charge (Note 18)
6859 
6860 
6861 
6862 
6863 
6864 
6865 
6866 
6867 
6868 
6869 
6870 
6871 
6872 
6873 
6874 
6875 1,873
6876 
6877 
6878 
6879 
6880 
6881 
6882 
6883 
6884 1,873
6885 
6886 
6887 
6888 
6889 
6890 1,873
6891 
6892 
6893 
6894 
6895 Reversal of stock-based compensation charge (Note 18)
6896 
6897 (17,500
6898 )
6899 
6900 
6901 
6902 
6903 
6904 
6905 
6906 
6907 
6908 
6909 (17,500
6910 )
6911 
6912 (145
6913 )
6914 
6915 
6916 
6917 
6918 
6919 
6920 
6921 (145
6922 )
6923 
6924 
6925 
6926 
6927 (145
6928 )
6929 
6930 
6931 
6932 Stock-based compensation charge related to equity accounted investment (Note 10)
6933 
6934 
6935 
6936 
6937 
6938 
6939 
6940 
6941 
6942 
6943 
6944 
6945 
6946 
6947 
6948 
6949 71
6950 
6951 
6952 
6953 
6954 
6955 


...

96064 us-gaap_ValuationAllowanceDeferredTaxAssetChangeInAmount
96065 Namespace Prefix:
96066 us-gaap_
96067 Data Type:
96068 xbrli:monetaryItemType
96069 Balance Type:
96070 credit
96071 Period Type:
96072 duration
96073 X
96074 - DefinitionLine items represent financial concepts included in a table. These concepts are used to disclose reportable information associated with domain members defined in one or many axes to the table.
+ ReferencesNo definition available.
+ Details

 Name:
us-gaap_ValuationAllowanceLineItems


 Namespace Prefix:
us-gaap_


 Data Type:
xbrli:stringItemType


 Balance Type:
na


 Period Type:
duration
96075 Name:
96076 us-gaap_ValuationAllowanceLineItems
96077 Namespace Prefix:
96078 us-gaap_
96079 Data Type:
96080 xbrli:stringItemType
96081 Balance Type:
96082 na
96083 Period Type:
96084 duration
96085 X
96086 - Details

 Name:
srt_StatementScenarioAxis=ueps_AdditionalMember


 Namespace Prefix:



 Data Type:
na


 Balance Type:



 Period Type:
96087 Name:


97564 
97565 56,003
97566 55,963
97567 
97568 55,860
97569 
97570 Stock options
97571 
97572 
97573 
97574 
97575 
97576 
97577 
97578 
97579 0
97580 18
97581 
97582 51
97583 
97584 Denominator for diluted (loss) earnings per share: adjusted weighted average common shares outstanding and assuming conversion
97585 
97586 
97587 
97588 
97589 
97590 
97591 
97592 
97593 56,003
97594 55,981
97595 
97596 55,911
97597 
97598 (Loss) Earnings per share: Basic
97599 $ (0.68)
97600 $ (0.61)
97601 $ 0
97602 $ (0.08)
97603 $ (3.22)
97604 $ (1.03)
97605 $ (1.12)
97606 $ (0.09)
97607 $ (1.37)
97608 $ (5.48)
97609 [1]
97610 $ 1.1
97611 [1]
97612 Continuing
97613 (0.68)
97614 (0.85)
97615 (0.05)
97616 (0.13)
97617 (3.24)
97618 (0.9)
97619 (1.17)
97620 (0.17)
97621 (1.7)
97622 (5.49)
97623 [1]
97624 0.92
97625 [1]
97626 Discontinued
97627 0
97628 0.24
97629 0.05
97630 0.05
97631 0.02
97632 (0.13)
97633 0.05
97634 0.08
97635 0.33
97636 0.01
97637 [1]
97638 0.18
97639 [1]
97640 (Loss) Earnings per share

98851 Segment Reporting, Revenue Reconciling Item [Line Items]
98852 
98853 
98854 
98855 Revenues
98856 0
98857 0
98858 0
98859 Inter-Segment [Member] | South African Transaction Processing [Member]
98860 
98861 
98862 
98863 Segment Reporting, Revenue Reconciling Item [Line Items]
98864 
98865 
98866 
98867 Revenues
98868 (7,956)
98869 (6,990)
98870 (29,949)
98871 Inter-Segment [Member] | International Transaction Processing [Member]
98872 
98873 
98874 
98875 Segment Reporting, Revenue Reconciling Item [Line Items]
98876 
98877 
98878 
98879 Revenues
98880 0
98881 0
98882 0
98883 Inter-Segment [Member] | International Transaction Processing [Member] | Continuing [Member]
98884 
98885 
98886 
98887 Segment Reporting, Revenue Reconciling Item [Line Items]
98888 
98889 
98890 
98891 Revenues
98892 0
98893 0
98894 0
98895 Inter-Segment [Member] | International Transaction Processing [Member] | Discontinued [Member]
98896 
98897 
98898 
98899 Segment Reporting, Revenue Reconciling Item [

100467 Operating (loss) income
100468 
100469 
100470 
100471 
100472 
100473 
100474 
100475 
100476 (9,433)
100477 (48,501)
100478 
100479 (13,904)
100480 
100481 Depreciation and amortization
100482 
100483 
100484 
100485 
100486 
100487 
100488 
100489 
100490 (265)
100491 (6,882)
100492 
100493 (3,657)
100494 
100495 Corporate/Eliminations [Member] | Discontinued [Member]
100496 
100497 
100498 
100499 
100500 
100501 
100502 
100503 
100504 
100505 
100506 
100507 
100508 
100509 Segment Reporting Information [Line Items]
100510 
100511 
100512 
100513 
100514 
100515 
100516 
100517 
100518 
100519 
100520 
100521 
100522 
100523 Operating (loss) income
100524 
100525 
100526 
100527 
100528 
100529 
100530 
100531 
100532 (5,784)
100533 (22,315)
100534 
100535 (12,837)
100536 
100537 Depreciation and amortization
100538 
100539 
100540 
100541 
100542 
100543 
100544 
100545 
100546 (4,749)
100547 (14,925)
100548 
100549 (8,134)
100550 
100551 South African Transaction Process

102151 $ 0.24
102152 $ 0.05
102153 $ 0.05
102154 $ 0.02
102155 $ (0.13)
102156 $ 0.05
102157 $ 0.08
102158 $ 0.33
102159 $ 0.01
102160 [1]
102161 $ 0.17
102162 [1]
102163 Segment Continuing Operations [Member] | Refund [Member]
102164 
102165 
102166 
102167 
102168 
102169 
102170 
102171 
102172 
102173 
102174 
102175 
102176 
102177 Selected Quarterly Financial Information [Line Items]
102178 
102179 
102180 
102181 
102182 
102183 
102184 
102185 
102186 
102187 
102188 
102189 
102190 
102191 Revenue
102192 
102193 
102194 
102195 
102196 $ 19,709
102197 
102198 
102199 
102200 
102201 
102202 
102203 
102204 
102205 
102206 [1]
Refer to Note 1
102207 [1]
102208 Refer to Note 1
102209 X
102210 - ReferencesNo definition available.
+ Details

 Name:
ueps_SelectedQuarterlyFinancialInformationLineItems


 Namespace Prefix:
ueps_


 Data Type:
xbrli:stringItemType


 Balance Type:
na


 Period Type:
duration
102211 Name:
102212 ueps_SelectedQuarterlyFinancialInformationLineItems
10221

In [ ]:
res = {}

for file_doc in soup.find_all('document'):
    

    doc_dict = {
        'file_name' : file_doc.filename.find(text=True, recursive=False).strip(),
        'type' : file_doc.type.find(text=True, recursive=False).strip(),
        'sequence' : file_doc.sequence.find(text=True, recursive=False).strip(),
        'description' : file_doc.description.find(text=True, recursive=False).strip(),
        'code' : file_doc.find('text'),
    }

    # filing text
    file_text = doc_dict['code']

    # thematic breaks
    thm_breaks = file_text.find_all(('hr'), {'width':'100%'})
    thm_breaks = [str(thm_break) for thm_break in thm_breaks]

    file_str = str(file_doc)

    if len(thm_breaks) > 0:

        re_delimit = '|'.join(map(re.escape, thm_breaks))

        doc_dict['page_code'] = re.split(re_delimit, file_str)

    else:

        doc_dict['page_code'] = [thm_breaks]
        
    res[doc_dict['file_name']] = doc_dict
    

In [ ]:
file_doc = res['R3.htm']['code']

table_dict = {}

table = file_doc.find_all('table')[0]

table_dict.update({
    'id' : table.get('id'),
    'class' : table.get('class')
})

row_data = []
for row in table.find_all('tr'):

    table_headers = [th.text.strip() for th in row.find_all('th')]
    table_data = [td.text.strip() for td in row.find_all('td')]
    
    if table_data:
        row_data.append(table_data)
    else:
        row_data.append(table_headers)
    

In [ ]:
tables = pd.read_html(str(file_doc))

for tb in tables:
    
    if len(tb.columns):
        tb = tb.set_index(tb.columns[0])
        
    display(tb)

In [ ]:
tables_dict = {}

tables = pd.read_html(data)

for tb in tables:
    
    if len(tb.columns):
        tb = tb.set_index(tb.columns[0])
        
    tables_dict[tb.index.name] = tb

In [ ]:
for k, v in tables_dict.items():
    print(v.index.name, '\n')
    print(v.columns, '\n')
    display(v)